In [76]:
# GCN model
# 환경설정을 PIP 기반으로 간략하게 변경하였음

import os
import sys
import torch

# Check the compatibility of the python and torch version (Comments are wriiten @2024.08.30)
print("Python version: {}".format(sys.version))                    # 3.10.12
print("PyTorch version:{}".format(torch.__version__))              # 2.4.0+cu124
print("cuda version:   {}".format(torch.version.cuda))             # 12.1
print("cudnn version:  {}".format(torch.backends.cudnn.version())) # 8700

# Install required python libraries
!pip install -q pyg_lib -f https://data.pyg.org/whl/torch-2.4.0+cu121.html
!pip install -q torch_scatter -f https://data.pyg.org/whl/torch-2.4.0+cu121.html
!pip install -q torch_sparse  -f https://data.pyg.org/whl/torch-2.4.0+cu121.html
!pip install -q torch_cluster -f https://data.pyg.org/whl/torch-2.4.0+cu121.html
!pip install -q torch_spline_conv -f https://data.pyg.org/whl/torch-2.4.0+cu121.html
!pip install -q torch-geometric
!pip install -q e3nn vapeplot
!pip install rdkit

# Check the compatibilites of the torch-geometric
import torch_geometric as pyg
print("torch_geometric version:{}".format(pyg.__version__))        # 2.4.0

Python version: 3.9.23 (main, Jun  5 2025, 13:40:20) 
[GCC 11.2.0]
PyTorch version:2.8.0+cu128
cuda version:   12.8
cudnn version:  91002
torch_geometric version:2.6.1


In [77]:
import os
import numpy as np
import pandas as pd
import json,pickle
import networkx as nx
from math import sqrt
from random import shuffle
from collections import OrderedDict
from scipy import stats
from IPython.display import SVG
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.nn import Sequential, Linear, ReLU
from sklearn.model_selection import train_test_split

In [78]:
from rdkit import Chem
from rdkit.Chem.Draw import IPythonConsole
from rdkit.Chem import rdDepictor
from rdkit.Chem.Draw import rdMolDraw2D
from rdkit.Chem import MolFromSmiles
from torch_geometric import data as DATA
from torch_geometric.data import InMemoryDataset
from torch_geometric.loader import DataLoader
from torch_geometric.nn import GCNConv, global_max_pool as gmp
from torch_geometric.nn import GCNConv, GATConv, GINConv, global_add_pool
from torch_geometric.nn import global_mean_pool as gap, global_max_pool as gmp

# 시각화 라이브러리
from matplotlib import pyplot as plt
import seaborn as sns
%matplotlib inline

In [79]:
df = pd.read_csv('./data/kiba.tab', sep="\t")

In [80]:
df

ID1                                                 X1  \
0       CHEMBL1087421            COc1cc2c(cc1Cl)C(c1ccc(Cl)c(Cl)c1)=NCC2   
1       CHEMBL1087421            COc1cc2c(cc1Cl)C(c1ccc(Cl)c(Cl)c1)=NCC2   
2       CHEMBL1087421            COc1cc2c(cc1Cl)C(c1ccc(Cl)c(Cl)c1)=NCC2   
3       CHEMBL1087421            COc1cc2c(cc1Cl)C(c1ccc(Cl)c(Cl)c1)=NCC2   
4       CHEMBL1087421            COc1cc2c(cc1Cl)C(c1ccc(Cl)c(Cl)c1)=NCC2   
...               ...                                                ...   
117652   CHEMBL230654  CCCc1nc[nH]c1CNc1cc(Cl)c2ncc(C#N)c(Nc3ccc(F)c(...   
117653   CHEMBL230654  CCCc1nc[nH]c1CNc1cc(Cl)c2ncc(C#N)c(Nc3ccc(F)c(...   
117654   CHEMBL230654  CCCc1nc[nH]c1CNc1cc(Cl)c2ncc(C#N)c(Nc3ccc(F)c(...   
117655   CHEMBL230654  CCCc1nc[nH]c1CNc1cc(Cl)c2ncc(C#N)c(Nc3ccc(F)c(...   
117656   CHEMBL230654  CCCc1nc[nH]c1CNc1cc(Cl)c2ncc(C#N)c(Nc3ccc(F)c(...   

           ID2                                                 X2         Y  
0       O00141  MTVKTEAAKGTLTYSRMRGMVAILIAFMKQRRMGLNDFIQKIANNS...  11.10000  
1       O14920  MSWSPSLTTQTCGAWEMKERLGTGGFGNVIRWHNQETGEQIAIKQC...  11.10000  
2       O15111  MERPPGLRPGAGGPWEMRERLGTGGFGNVCLYQHRELDLKIAIKSC...  11.10000  
3       P00533  MRPSGTAGAALLALLAALCPASRALEEKKVCQGTSNKLTQLGTFED...  11.10000  
4       P04626  MELAALCRWGLLLALLPPGAASTQVCTGTDMKLRLPASPETHLDML...  11.10000  
...        ...                                                ...       ...  
117652  Q13554  MATTVTCTRFTDEYQLYEDIGKGAFSVVRRCVKLCTGHEYAAKIIN...  10.49794  
117653  Q13555  MATTATCTRFTDDYQLFEELGKGAFSVVRRCVKKTSTQEYAAKIIN...  10.49794  
117654  Q13557  MASTTTCTRFTDEYQLFEELGKGAFSVVRRCMKIPTGQEYAAKIIN...  10.49794  
117655  Q16539  MSQERPTFYRQELNKTIWEVPERYQNLSPVGSGAYGSVCAAFDTKT...  10.49794  
117656  Q9UQM7  MATITCTRFTEEYQLFEELGKGAFSVVRRCVKVLAGQEYAAKIINT...  10.49794  

[117657 rows x 5 columns]

In [81]:
# Split into train and test (80/20 split)
train_df, temp_df = train_test_split(df, test_size=0.2, random_state=42)
# 2차 분할: temp -> test 10%, validation 10%
test_df, val_df = train_test_split(temp_df, test_size=0.5, random_state=42)
# Save as CSV files
train_path = './data/kiba_train.csv'
test_path = './data/kiba_test.csv'
val_path = './data/kiba_val.csv'

train_df.to_csv(train_path, index=False)
test_df.to_csv(test_path, index=False)
val_df.to_csv(val_path, index=False)

In [82]:
kiba_train = pd.read_csv('./data/kiba_train.csv')
kiba_test = pd.read_csv('./data/kiba_test.csv')
kiba_val = pd.read_csv('./data/kiba_val.csv')

#### 원자 특성 인코딩

In [83]:
def feature_encoding(x, allowable_set):
    if x not in allowable_set:
        raise Exception("input{0} not allowed in set {1}:".format(x, allowable_set))
    return list(map(lambda s: x == s, allowable_set))

In [84]:
def feature_encoding_unk(x, allowable_set):
    # allowable set에 있지 않으면 마지막 요소로 매핑
    if x not in allowable_set:
        x = allowable_set[-1]
    return list(map(lambda s: x == s, allowable_set))

In [85]:
def atom_features(atom):
    return np.array(feature_encoding_unk(atom.GetSymbol(),['C', 'N', 'O', 'S', 'F', 'Si', 'P', 'Cl', 'Br', 'Mg', 'Na','Ca', 'Fe', 'As', 'Al', 'I', 'B', 'V', 'K', 'Tl', 'Yb','Sb', 'Sn', 'Ag', 'Pd', 'Co', 'Se', 'Ti', 'Zn', 'H','Li', 'Ge', 'Cu', 'Au', 'Ni', 'Cd', 'In', 'Mn', 'Zr','Cr', 'Pt', 'Hg', 'Pb', 'Unknown']) +
                    feature_encoding(atom.GetDegree(), [0,1,2,3,4,5,6,7,8,9,10]) +
                    feature_encoding_unk(atom.GetDegree(), [0,1,2,3,4,5,6,7,8,9,10]) +
                    feature_encoding_unk(atom.GetTotalNumHs(),[0,1,2,3,4,5,6,7,8,9,10]) +
                    feature_encoding_unk(atom.GetImplicitValence(),[0,1,2,3,4,5,6,7,8,9,10]) +
                    [atom.GetIsAromatic()]
                    )

#### SMILES to Graph

In [86]:
# returns: 원자 개수, 원자 특성 행렬, 인접 행렬
def smiles_to_graph(smiles):
    # 문자열 -> 그래프
    mol = Chem.MolFromSmiles(smiles)

    # 원자 개수 저장
    c_size = mol.GetNumAtoms()
    features = []

    for atom in mol.GetAtoms():
        feature = atom_features(atom)
        features.append(feature/sum(feature)) # 정규화

    # 엣지 - 시작 원자 정보와 끝 원자 정보
    edges = []
    for bond in mol.GetBonds():
        edges.append([bond.GetBeginAtomIdx(), bond.GetEndAtomIdx()])

    # nx라이브러리를 이용해 데이터를 방향 그래프로 변환
    g = nx.Graph(edges).to_directed()
    edge_index = []
    for e1, e2 in g.edges:
        edge_index.append([e1, e2])

    return c_size, features, edge_index

#### 데이터셋 구성

In [87]:
compound_smiles = []

opts = ['train','test']
for opt in opts:
    df = pd.read_csv('./data/kiba' + '_' + opt + '.csv')
    compound_smiles += list(df['X1'])
compound_smiles = set(compound_smiles) # 중복제거

smile_graph = {}

for smile in compound_smiles:
    g = smiles_to_graph(smile)
    smile_graph[smile] = g

[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValen

[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValence(getExplicit=False)
[03:39:57] DEPRECATION WARNING: please use GetValen

#### Protein Representation

In [88]:
# 표적 염기서열을 이루는 알파벳(25자) vocabulary
seq_voc = "ABCDEFGHIKLMNOPQRSTUVWXYZ"

# 정수로 매핑
seq_dict = {v:{i+1} for i,v in enumerate(seq_voc)}
seq_dict_len = len(seq_dict)

# padding
max_seq_len = 1000

In [89]:
# protein representation
def seq_cat(prot):
    # 0행렬 생성
    x = np.zeros(max_seq_len)
    for i, ch in enumerate(prot[:max_seq_len]):
        x[i] = seq_dict[ch]
    return x

In [90]:
# # datasets
# all_prots = []
# datasets = ['kiba']

In [91]:
class ProteinESMLinear(nn.Module):
    def __init__(self, in_dim=1280, out=256, dropout=0.2):
        super().__init__()
        self.net = nn.Sequential(
            nn.Linear(in_dim,1024),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(1024, out)
        )
    def forward(self, esm_repr): # [B, 1280] 형태로 넣어주기 (mean-pooled)
        return self.net(esm_repr)

In [92]:
# class DTIDataset(InMemoryDataset):
#     def __init__(self, csv_path, esm, transform = None, pre_transform=None):
#         super().__init__('.', transform, pre_transform)
#         self.df = pd.read_csv(csv_path)
#         if isinstance(esm, str):
#             if esm.endswith('.npy'):
#                 self.esm = np.load(esm, allow_pickle=True).item()

In [108]:
class TestbedDataset(InMemoryDataset):
    def __init__(self, root='/tmp', dataset='kiba', xd=None, xt=None, y=None, transform=None, pre_transform=None, smile_graph=None):
        super(TestbedDataset, self).__init__(root, transform, pre_transform)

        self.dataset = dataset

        if os.path.isfile(self.processed_paths[0]):
            print('pre-processed data found, loading...')
            self.data, self.slices = torch.load(self.processed_paths[0])
        else:
            print('pre-processed data not found, processing...')
            self.process(xd, xt, y, smile_graph)
            self.data, self.slices = torch.load(self.processed_paths[0])
            # XD : SMILES 목록
        # XT : 인코딩된 단백질(표적) 목록(one-hot encoding)
        # Y : 레이블 목록(결합 친화도)
        # Return : PyTorch-Geometric 형식으로 처리된 데이터

    def _process(self): #??
        if not os.path.exists(self.processed_dir):
            os.makedirs(self.processed_dir)

    def process(self, xd, xt, y, smile_graph):
        assert (len(xd) == len(xt) and len(xd) == len(y)), "Input lists must have the same length"
        data_list = []
        data_len = len(xd)

        # Graph Convolutional Networks Model의 입력 형식에 맞게 데이터 변환
        for i in range(data_len):
            print('converting SMILES to Graph...')
            smiles = xd[i]
            target = xt[i]
            labels = y[i]
            # smile_graph : RDKit을 활용하여 분자 그래프 표현으로 변환된 SMILES 값
            c_size, features, edge_index = smile_graph[smiles]
            # x : 특성 행렬
            GCNData = DATA.Data(x = torch.Tensor(features), 
                                edge_index=torch.LongTensor(edge_index).transpose(1,0),
                                y=torch.FloatTensor([labels]))
            GCNData.target = torch.LongTensor([target])

            GCNData.__setitem__('c_size', torch.LongTensor([c_size]))

            data_list.append(GCNData)
        if self.pre_filter is not None:
            data_list = [data for data in data_list if self.pre_filter(data)]

        if self.pre_transform is not None:
            data_list = [self.pre_transform(data) for data in data_list]

        print('Graph construction done. Saving to file.')
        data, slices = self.collate(data_list)

        # 전처리 데이터 저장
        torch.save((data, slices), self.processed_paths[0])


In [96]:
datasets = ['kiba']

# 전처리 데이터 로드
processed_data_file_train = './data/processed/' + datasets[0] + '_train.pt'
processed_data_file_test = './data/processed/' + datasets[0] + '_test.pt'

if ((not os.path.isfile(processed_data_file_train)) or (not os.path.isfile(processed_data_file_test))):
    df = pd.read_csv('./data/' + datasets[0] + '_train.csv')
    train_drugs, train_prots,  train_Y = list(df['X1']),list(df['X2']),list(df['Y'])
    XT = [seq_cat(t) for t in train_prots]
    train_drugs, train_prots,  train_Y = np.asarray(train_drugs), np.asarray(XT), np.asarray(train_Y)

    df = pd.read_csv('./data/' + datasets[0] + '_test.csv')
    test_drugs, test_prots,  test_Y = list(df['X1']),list(df['X2']),list(df['Y'])
    XT = [seq_cat(t) for t in test_prots]
    test_drugs, test_prots,  test_Y = np.asarray(test_drugs), np.asarray(XT), np.asarray(test_Y)

    # PyTorch Geometric 데이터 생성
    print('preparing ', datasets[0] + '_train.pt in pytorch format!')
    train_data = TestbedDataset(root='/content/drive/My Drive/GraphDTA/data', dataset=datasets[0] + '_train', xd=train_drugs, xt=train_prots, y=train_Y,smile_graph=smile_graph)
    print('preparing ', datasets[0] + '_test.pt in pytorch format!')
    test_data = TestbedDataset(root='/content/drive/My Drive/GraphDTA/data', dataset=datasets[0]+'_test', xd=test_drugs, xt=test_prots, y=test_Y,smile_graph=smile_graph)
    print(processed_data_file_train, ' and ', processed_data_file_test, ' have been created')
else:
    print(processed_data_file_train, ' and ', processed_data_file_test, ' are already created')

TypeError: float() argument must be a string or a number, not 'set'

#### 평가지표들

In [107]:
def mse(y,f):
    mse = ((y - f)**2).mean(axis=0)
    return mse

In [106]:
def rmse(y,f):
    rmse = sqrt(((y - f)**2).mean(axis=0))
    return rmse

In [105]:
def pearson(y,f):
    rp = np.corrcoef(y, f)[0,1]
    return rp

In [104]:
def spearman(y,f):
    rs = stats.spearmanr(y, f)[0]
    return rs

In [103]:
def ci(y,f):
    ind = np.argsort(y)
    y = y[ind]
    f = f[ind]
    i = len(y)-1
    j = i-1
    z = 0.0
    S = 0.0
    while i > 0:
        while j >= 0:
            if y[i] > y[j]:
                z = z+1
                u = f[i] - f[j]
                if u > 0:
                    S = S + 1
                elif u == 0:
                    S = S + 0.5
            j = j - 1
        i = i - 1
        j = i-1
    ci = S/z
    return ci

In [102]:
class GCN(torch.nn.Module):
    def __init__(self, n_output = 1, n_filters=32, embed_dim=128, num_features_xd=78, num_features_xt = 25, output_dim=128, dropout=0.2, esm_in_dim=1280):
        super(GCN, self).__init__()
        self.n_output = n_output # 모델의 출력은 숫자 1개

        # Drug Representation
        self.conv1 = GCNConv(num_features_xd, num_features_xd)
        self.conv2 = GCNConv(num_features_xd, num_features_xd*2)
        self.conv3 = GCNConv(num_features_xd*2, num_features_xd*4)

        # fully connected layer - 1024차원으로 변환
        self.fc_g1 = torch.nn.Linear(num_features_xd*4, 1024)
        self.fc_g2 = torch.nn.Linear(1024, output_dim)

        # activation function
        self.relu = nn.ReLU()
        #Dropout
        self.dropout = nn.Dropout(dropout)

        # Protein Representation(ESM -> MLP proj)
        self.protein_proj = nn.Sequential(
            nn.Linear(esm_in_dim, 1024),
            nn.ReLU(),
            nn.Dropout(dropout),
            nn.Linear(1024, output_dim)
        )

        # Drug + Protein Representation fusion
        self.fc1 = nn.Linear(2*output_dim, 1024)
        self.fc2 = nn.Linear(1024,512)

        self.out = nn.Linear(512, self.n_output)
    def forward(self, data):
        x, edge_index, batch = data.x, data.edge_index, data.batch
        # target = data.target

        # GCN Layer
        x = self.conv1(x, edge_index)
        x = self.relu(x)
        
        x = self.conv2(x, edge_index)
        x = self.relu(x)

        x = self.conv3(x, edge_index)
        x = self.relu(x)

        x = gmp(x, batch)

        x = self.relu(self.fc_g1(x))
        x = self.dropout(x)
        x = self.fc_g2(x)
        x = self.dropout(x)

        xt = data.protein_esm.float()
        xt = self.protein_proj(xt)

        # Drug, Protein Representation을 torch.cat을 이용해 하나로 결합
        xc = torch.cat((x, xt), 1)

        # 하나의 출력값 구하기
        xc = self.fc1(xc)
        xc = self.relu(xc)
        xc = self.dropout(xc)
        xc = self.fc2(xc)
        xc = self.relu(xc)
        xc = self.dropout(xc)
        out = self.out(xc)
        return out

In [ ]:
# def make_data_item(graph_x, edge_index, y, esm_vec):
#     d = Data(
#         x=torch.tensor(graph_x, dtype=torch.float),
#         edge_index=torch.tensor(edge_index, dtype=torch.long),
#         y=torch.tensor(y, dtype=torch.float)
#     )
#     d.protein_esm = torch.tensor(esm_vec, dtype=torch.float)
#     return d

In [101]:
def train(model, device, train_loader, optimizer, epoch):
    print('Training on {} samples...'.format(len(train_loader.dataset)))
    model.train()

    for batch_idx, data in enumerate(train_loader):
        data = data.to(device)

        optimizer.zero_grad()
        output = model(data)

        loss = loss_fn(output, data.y.view(-1,1).float().to(device))

        loss.backward()
        optimizer.step()

        if batch_idx%LOG_INTERVAL == 0:
            print('Train epoch: {}[{}/{} ({:.0f}%)]|tLoss: {:.6f}'.format(epoch,
                                                                          batch_idx*len(data.x),
                                                                          len(train_loader.dataset),
                                                                          100.*batch_idx/len(train_loader),
                                                                          loss.item()))

In [100]:
def predicting(model, device, loader):
    model.eval()
    total_preds = torch.Tensor()

    print('Make prediction for {} samples...'.format(len(loader.dataset)))
    with torch.no_grad():
        for data in loader:
            data = data.to(device)
            output = model(data)
            total_preds = torch.cat((total_preds, output.cpu()), 0)
            total_labels = torch.cat((total_labels, data.y.view(-1, 1).cpu()), 0)
    return total_labels.numpy().flatten(), total_preds.numpy().flatten()

In [ ]:
datasets = ['kiba']
modelling = [GCN]
cuda_name = "cuda:0"

### Main

In [97]:
Train_Batch_Size = 512
Test_Batch_Size = 512
LR = 0.0005
Log_Interval = 20
Num_Epochs = 10

In [98]:
processed_data_file_train = './data/' + datasets[0] + '_train.pt'
processed_data_file_test = './data/' + datasets[0] + '_test.pt'

In [99]:
train_data = TestbedDataset(root='./data/', dataset=datasets[0]+'_train')
test_data = TestbedDataset(root='./data/', dataset=datasets[0]+'_test')

train_loader = DataLoader(train_data, batch_size=Train_Batch_Size, shuffle=True)
test_loader = DataLoader(test_data, batch_size=Test_Batch_Size, shuffle=False)

device = torch.device(cuda_name if torch.cuda.is_available() else 'cpu')
model = modelling[0]().to(device)

loss_fn = nn.MSELoss()

optimizer = torch.optim.Adam(model.parameters(), lr=LR)

best_mse = 1000
best_ci = 0
best_epoch = -1

model_file_name = 'model_' + modelling[0] + '_' + 'kiba.model'
result_file_name = 'result_' + modelling[0] + '_' + 'kiba.csv'

NotImplementedError: 

In [109]:
for epoch in range(Num_Epochs):
    train(model, device, train_loader, optimizer, epoch + 1)

    G, P = predicting(model, device, test_loader)

    ret = [rmse(G,P), mse(G,P), pearson(G,P), spearman(G,P)]

    if ret[1] < best_mse:
        torch.save(model.state_dict(), model_file_name)
        with open(result_file_name, 'w') as f:
            f.write(','.join(map(str,ret)))
        best_mse = ret[1]
        best_ci = ret[-1]
        best_epoch = epoch + 1
        torch.save(model.state_dict(), model_file_name)
        print('rmse improved at epoch ', best_epoch, '; best_mse,best_ci:', best_mse,best_ci,modelling[0],datasets[0])
    else:
        print(ret[1],'No improvement since epoch ', best_epoch, '; best_mse,best_ci:', best_mse,best_ci,modelling[0],datasets[0])

NameError: name 'model' is not defined